In [2]:
import sys
import cv2
import numpy as np
import matplotlib.pyplot as plt
from skimage.segmentation import slic
from skimage.segmentation import mark_boundaries
from skimage.data import astronaut
from skimage.util import img_as_float
import maxflow
from scipy.spatial import Delaunay
from skimage import img_as_ubyte
np.set_printoptions(threshold=np.inf)
from skimage import io; io.use_plugin('matplotlib')


In [4]:
# Calculate the SLIC superpixels, their histograms and neighbors

# Calculate the SLIC superpixels, their histograms and neighbors
def superpixels_histograms_neighbors(img):
    # SLIC
    segments = slic(img, n_segments=502, compactness=18.5)
    segments_ids = np.unique(segments)

    # centers
    centers = np.array([np.mean(np.nonzero(segments==i),axis=1) for i in segments_ids])

    # H-S histograms for all superpixels
    hsv = cv2.cvtColor(img.astype('float32'), cv2.COLOR_BGR2HSV)
    bins = [24, 24] # H = S = 20
    ranges = [0, 360, 0, 1] # H: [0, 360], S: [0, 1]
    colors_hists = np.float32([cv2.calcHist([hsv],[0, 1], np.uint8(segments==i), bins, ranges).flatten() for i in segments_ids])

    # neighbors via Delaunay tesselation
    tri = Delaunay(centers)
    return (centers,colors_hists,segments,tri.vertex_neighbor_vertices)

# Get superpixels IDs for FG and BG from marking
def find_superpixels_under_marking(marking, superpixels):
    fg_segments = np.unique(superpixels[marking[:,:,0]!=255])
    bg_segments = np.unique(superpixels[marking[:,:,2]!=255])
    return (fg_segments, bg_segments)

# Sum up the histograms for a given selection of superpixel IDs, normalize
def cumulative_histogram_for_superpixels(ids, histograms):
    h = np.sum(histograms[ids],axis=0)
    return h / h.sum()

# Get a bool mask of the pixels for a given selection of superpixel IDs
def pixels_for_segment_selection(superpixels_labels, selection):
    pixels_mask = np.where(np.isin(superpixels_labels, selection), True, False)
    return pixels_mask

# Get a normalized version of the given histograms (divide by sum)
def normalize_histograms(histograms):
    return np.float32([h / h.sum() for h in histograms])

# Perform graph cut using superpixels histograms
def do_graph_cut(fgbg_hists, fgbg_superpixels, norm_hists, neighbors):
    num_nodes = norm_hists.shape[0]
    # Create a graph of N nodes, and estimate of 5 edges per node
    g = maxflow.Graph[float](num_nodes, num_nodes * 5)
    # Add N nodes
    nodes = g.add_nodes(num_nodes)

    hist_comp_alg = cv2.HISTCMP_KL_DIV

    # Smoothness term: cost between neighbors
    indptr,indices = neighbors
    for i in range(len(indptr)-1):
        N = indices[indptr[i]:indptr[i+1]] # list of neighbor superpixels
        hi = norm_hists[i]                 # histogram for center
        for n in N:
            if (n < 0) or (n > num_nodes):
                continue
            # Create two edges (forwards and backwards) with capacities based on
            # histogram matching
            hn = norm_hists[n]             # histogram for neighbor
            g.add_edge(nodes[i], nodes[n], 20-cv2.compareHist(hi, hn, hist_comp_alg),
                                           20-cv2.compareHist(hn, hi, hist_comp_alg))

    # Match term: cost to FG/BG
    for i,h in enumerate(norm_hists):
        if i in fgbg_superpixels[0]:
            g.add_tedge(nodes[i], 0, 1000) # FG - set high cost to BG
        elif i in fgbg_superpixels[1]:
            g.add_tedge(nodes[i], 1000, 0) # BG - set high cost to FG
        else:
            g.add_tedge(nodes[i], cv2.compareHist(fgbg_hists[0], h, hist_comp_alg),
                                  cv2.compareHist(fgbg_hists[1], h, hist_comp_alg))


    g.maxflow()
    return g.get_grid_segments(nodes)




In [50]:
oriimg = cv2.imread("resized_img_mask.png", cv2.IMREAD_COLOR)
oriimg

array([[[  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],
        [  0,   0,   0],


In [49]:
img = cv2.imread("astronaut.png", cv2.IMREAD_COLOR)
img

array([[[151, 147, 154],
        [102,  58,  63],
        [106,  76,  76],
        [122, 121, 124],
        [138, 141, 148],
        [111, 115, 123],
        [ 73,  56,  62],
        [ 25,   2,   8],
        [  7,   1,   2],
        [  9,   1,   3],
        [ 33,   4,  13],
        [ 51,   9,  22],
        [ 44,   8,  18],
        [ 47,   8,  20],
        [ 41,   6,  17],
        [ 54,  11,  24],
        [ 66,  42,  51],
        [ 67,  55,  64],
        [ 38,  10,  19],
        [ 33,   4,  13],
        [ 83,  68,  79],
        [128, 124, 141],
        [145, 148, 159],
        [148, 151, 162],
        [155, 153, 163],
        [161, 160, 166],
        [157, 158, 161],
        [159, 159, 164],
        [162, 158, 163],
        [164, 160, 164],
        [161, 159, 165],
        [156, 158, 163],
        [164, 160, 164],
        [160, 162, 164],
        [165, 162, 164],
        [163, 163, 165],
        [171, 167, 169],
        [166, 166, 168],
        [167, 168, 170],
        [168, 166, 169],


In [68]:
img_new = cv2.resize(oriimg, None, fx=0.5, fy=0.5, interpolation=cv2.INTER_AREA)
cv2.imwrite("white.png", img_new);

In [59]:
import imutils
img = cv2.imread("new_img.png", cv2.IMREAD_COLOR)
img = imutils.resize(img, width=256, height=256)
cv2.imwrite('resized_img.png' , img)


True

In [51]:
!pip3 install imutils

You should consider upgrading via the 'pip install --upgrade pip' command.


In [194]:
oriimg = cv2.imread("img1_mask.png", cv2.IMREAD_COLOR)
oriimg.shape

(542, 404, 3)

In [195]:
oriimg = cv2.imread("image1.png", cv2.IMREAD_COLOR)
oriimg.shape

(1024, 768, 3)

In [9]:
oriimg = cv2.imread("resized_img.png", cv2.IMREAD_COLOR)
dim = (224, 224)
# resize image
resized = cv2.resize(oriimg, dim, interpolation = cv2.INTER_AREA)
 
print('Resized Dimensions : ',resized.shape)
 
cv2.imwrite('resized_img.png' , resized)

Resized Dimensions :  (224, 224, 3)


True

In [8]:
oriimg = cv2.imread("pytorch_out.png", cv2.IMREAD_COLOR)
oriimg.shape

(224, 224, 3)

In [3]:
    
    img = cv2.imread("resized_img.png", cv2.IMREAD_COLOR)
    img_marking = cv2.imread("white.png", cv2.IMREAD_COLOR)

    # ======================================== #
    # write all your codes here

    centers, color_hists, superpixels, neighbors = superpixels_histograms_neighbors(img)
    norm_hists = normalize_histograms(color_hists)
    fg_segments, bg_segments = find_superpixels_under_marking(img_marking, superpixels)

    fg_cumulative_hist = cumulative_histogram_for_superpixels(fg_segments, color_hists)
    bg_cumulative_hist = cumulative_histogram_for_superpixels(bg_segments, color_hists)
    
    fgbg_hists = {}
    fgbg_hists[0] = fg_cumulative_hist
    fgbg_hists[1] = bg_cumulative_hist

    fgbg_superpixels = {}
    fgbg_superpixels[0] = fg_segments
    fgbg_superpixels[1] = bg_segments

    graph_cut = do_graph_cut(fgbg_hists, fgbg_superpixels, norm_hists, neighbors)
    mask = pixels_for_segment_selection(superpixels, np.nonzero(graph_cut))
    mask = np.uint8(mask * 255)
    # ======================================== #

    # read video file
    output_name = "out1.png"
    cv2.imwrite(output_name, mask);

NameError: name 'superpixels_histograms_neighbors' is not defined

In [10]:
src1 = cv2.imread("resized_img.png", cv2.IMREAD_COLOR)

src1_mask = cv2.imread("pytorch.out.png", cv2.COLOR_GRAY2BGR)


In [12]:
#src1_mask=cv2.cvtColor(src1_mask,cv2.COLOR_GRAY2BGR)#change mask to a 3 channel image 
mask_out=cv2.subtract(src1_mask,src1)
mask_out=cv2.subtract(src1_mask,mask_out)
mask_out[src1_mask == 0] = 255

cv2.imwrite('res.png' , mask_out)


error: OpenCV(4.1.1) /Users/travis/build/skvark/opencv-python/opencv/modules/core/src/arithm.cpp:663: error: (-209:Sizes of input arguments do not match) The operation is neither 'array op array' (where arrays have the same size and the same number of channels), nor 'array op scalar', nor 'scalar op array' in function 'arithm_op'


In [159]:
src1 = cv2.imread("out1.png", cv2.IMREAD_COLOR)
src1[src1 == 0] = 255
cv2.imwrite('white.png' , src1)

True

In [190]:
# USAGE
# python segment.py --model enet-cityscapes/enet-model.net --classes enet-cityscapes/enet-classes.txt --colors enet-cityscapes/enet-colors.txt --image images/example_01.png
# import the necessary packages
import numpy as np
import argparse
import imutils
import time
import cv2

# construct the argument parse and parse the arguments
ap = argparse.ArgumentParser()
ap.add_argument("-m", "--model", required=True,
    help="path to deep learning segmentation model")
ap.add_argument("-c", "--classes", required=True,
    help="path to .txt file containing class labels")
ap.add_argument("-i", "--image", required=True,
    help="path to input image")
ap.add_argument("-l", "--colors", type=str,
    help="path to .txt file containing colors for labels")
ap.add_argument("-w", "--width", type=int, default=500,
    help="desired width (in pixels) of input image")
args = vars(ap.parse_args())

# load the class label names
CLASSES = open(args["classes"]).read().strip().split("\n")

# if a colors file was supplied, load it from disk
if args["colors"]:
    COLORS = open(args["colors"]).read().strip().split("\n")
    COLORS = [np.array(c.split(",")).astype("int") for c in COLORS]
    COLORS = np.array(COLORS, dtype="uint8")

# otherwise, we need to randomly generate RGB colors for each class
# label
else:
    # initialize a list of colors to represent each class label in
    # the mask (starting with 'black' for the background/unlabeled
    # regions)
    np.random.seed(42)
    COLORS = np.random.randint(0, 255, size=(len(CLASSES) - 1, 3),
    dtype="uint8")
    COLORS = np.vstack([[0, 0, 0], COLORS]).astype("uint8")

# initialize the legend visualization
legend = np.zeros(((len(CLASSES) * 25) + 25, 300, 3), dtype="uint8")

# loop over the class names + colors
for (i, (className, color)) in enumerate(zip(CLASSES, COLORS)):
    # draw the class name + color on the legend
    color = [int(c) for c in color]
    cv2.putText(legend, className, (5, (i * 25) + 17),
    cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 2)
    cv2.rectangle(legend, (100, (i * 25)), (300, (i * 25) + 25),tuple(color), -1)

# load our serialized model from disk
print("[INFO] loading model...")
net = cv2.dnn.readNet(args["model"])

# load the input image, resize it, and construct a blob from it,
# but keeping mind mind that the original input image dimensions
# ENet was trained on was 1024x512
image = cv2.imread(args["image"])
image = imutils.resize(image, width=args["width"])
blob = cv2.dnn.blobFromImage(image, 1 / 255.0, (1024, 512), 0,swapRB=True, crop=False)

# perform a forward pass using the segmentation model
net.setInput(blob)
start = time.time()
output = net.forward()
end = time.time()

# show the amount of time inference took
print("[INFO] inference took {:.4f} seconds".format(end - start))

# infer the total number of classes along with the spatial dimensions
# of the mask image via the shape of the output array
(numClasses, height, width) = output.shape[1:4]

# our output class ID map will be num_classes x height x width in
# size, so we take the argmax to find the class label with the
# largest probability for each and every (x, y)-coordinate in the
# image
classMap = np.argmax(output[0], axis=0)

# given the class ID map, we can map each of the class IDs to its
# corresponding color
mask = COLORS[classMap]

# resize the mask and class map such that its dimensions match the
# original size of the input image (we're not using the class map
# here for anything else but this is how you would resize it just in
# case you wanted to extract specific pixels/classes)
mask = cv2.resize(mask, (image.shape[1], image.shape[0]),interpolation=cv2.INTER_NEAREST)
classMap = cv2.resize(classMap, (image.shape[1], image.shape[0]),
interpolation=cv2.INTER_NEAREST)

# perform a weighted combination of the input image with the mask to
# form an output visualization
output = ((0.4 * image) + (0.6 * mask)).astype("uint8")

# show the input and output images
cv2.imshow("Legend", legend)
cv2.imshow("Input", image)
cv2.imshow("Output", output)
cv2.waitKey(0)


usage: ipykernel_launcher.py [-h] -m MODEL -c CLASSES -i IMAGE [-l COLORS]
                             [-w WIDTH]
ipykernel_launcher.py: error: the following arguments are required: -m/--model, -c/--classes, -i/--image


SystemExit: 2

/usr/local/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3304: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [ ]:
oriimg = cv2.imread("resized_img.png", cv2.IMREAD_COLOR)
dim = (224, 224)
# resize image
resized = cv2.resize(oriimg, dim, interpolation = cv2.INTER_AREA)
 
print('Resized Dimensions : ',resized.shape)
 
cv2.imwrite('resized_img.png' , resized)